## Waits

In [15]:
SELECT
    [owt].[session_id],
    [owt].[exec_context_id],
    [ot].[scheduler_id],
    [owt].[wait_duration_ms],
    [owt].[wait_type],
    [owt].[blocking_session_id],
    [owt].[resource_description],
    CASE [owt].[wait_type]
        WHEN N'CXPACKET' THEN
            RIGHT ([owt].[resource_description],
                CHARINDEX (N'=', REVERSE ([owt].[resource_description])) - 1)
        ELSE NULL
    END AS [Node ID],
    --[es].[program_name],
      CASE   
     WHEN [statement_start_offset] > 0 THEN  
        --The start of the active command is not at the beginning of the full command text 
        CASE [statement_end_offset]  
           WHEN -1 THEN  
              --The end of the full command is also the end of the active statement 
              SUBSTRING(est.TEXT, ([statement_start_offset]/2) + 1, 2147483647) 
           ELSE   
              --The end of the active statement is not at the end of the full command 
              SUBSTRING(est.TEXT, ([statement_start_offset]/2) + 1, ([statement_end_offset] - [statement_start_offset])/2)   
        END  
     ELSE  
        --1st part of full command is running 
        CASE [statement_end_offset]  
           WHEN -1 THEN  
              --The end of the full command is also the end of the active statement 
              RTRIM(LTRIM(est.[text]))  
           ELSE  
              --The end of the active statement is not at the end of the full command 
              LEFT(est.TEXT, ([statement_end_offset]/2) +1)  
        END  
     END AS [executing statement],
    [er].[database_id],
    [eqp].[query_plan],
    [er].[cpu_time]
FROM sys.dm_os_waiting_tasks [owt]
INNER JOIN sys.dm_os_tasks [ot] ON
    [owt].[waiting_task_address] = [ot].[task_address]
INNER JOIN sys.dm_exec_sessions [es] ON
    [owt].[session_id] = [es].[session_id]
INNER JOIN sys.dm_exec_requests [er] ON
    [es].[session_id] = [er].[session_id]
OUTER APPLY sys.dm_exec_sql_text ([er].[sql_handle]) [est]
OUTER APPLY sys.dm_exec_query_plan ([er].[plan_handle]) [eqp]
WHERE
    [es].[is_user_process] = 1
ORDER BY
    [owt].[session_id],
    [owt].[exec_context_id];

(28 rows affected)

Total execution time: 00:00:00.3025898

session_id exec_context_id scheduler_id wait_duration_ms wait_type blocking_session_id resource_description Node ID executing statement database_id query_plan cpu_time 135 0 6 7 PAGELATCH_EX NULL 7:3:189315 NULL INSERT INTO dbo.TokenSearchParam
 (ResourceTypeId, ResourceSurrogateId, SearchParamId, CompositeInstanceId, System, Code, Text)
 SELECT @resourceTypeId, @resourceSurrogateId, SearchParamId, CompositeInstanceId, System, Code, Text 
 FROM @tvpTokenSearchPara 7 <ShowPlanXML xmlns="http://schemas.microsoft.com/sqlserver/2004/07/showplan" Version="1.524" Build="15.0.1300.542"><BatchSequence><Batch><Statements><StmtSimple StatementText="&#xD;&#xA;&#xD;&#xA;&#xD;&#xA;CREATE PROCEDURE dbo.UpsertResource&#xD;&#xA;&#x9;@resourceTypeId smallint,&#xD;&#xA;&#x9;@resourceId varchar(64),&#xD;&#xA;&#x9;@rawResource [varbinary](max),&#xD;&#xA;&#x9;@tvpStringSearchParam [dbo].[StringSearchParamTableType] READONLY,&#xD;&#xA;&#x9;@tvpTokenSearchParam [dbo].[TokenSearchParamTableType] READONLY,&#xD;&#xA;&#x9;@tvpDateSearchParam [dbo].[DateSearchParamTableType] READONLY,&#xD;&#xA;&#x9;@tvpReferenceSearchParam [dbo].[ReferenceSearchParamTableType] READONLY,&#xD;&#xA;&#x9;@tvpQuantitySearchParam [dbo].[QuantitySearchParamTableType] READONLY,&#xD;&#xA;&#x9;@tvpNumberSearchParam [dbo].[NumberSearchParamTableType] READONLY,&#xD;&#xA;&#x9;@tvpUriSearchParam [dbo].[UriSearchParamTableType] READONLY&#xD;&#xA;&#x9;AS&#xD;&#xA;&#x9;&#x9;SET XACT_ABORT ON&#xD;&#xA;&#x9;&#x9;" StatementId="1" StatementCompId="2" StatementType="SET ON/OFF" RetrievedFromCache="true" /><StmtSimple StatementText="BEGIN TRANSACTION&#xD;&#xA;&#xD;&#xA;&#x9;&#x9;" StatementId="2" StatementCompId="3" StatementType="BEGIN TRANSACTION" RetrievedFromCache="true" /><StmtSimple StatementText="DECLARE @version int = 1&#xD;&#xA;&#x9;&#x9;" StatementId="3" StatementCompId="4" StatementType="ASSIGN" RetrievedFromCache="true" /><StmtSimple StatementText="DECLARE @resourceSurrogateId bigint&#xD;&#xA;&#xD;&#xA;&#x9;&#x9;SELECT @version = (Version + 1), @resourceSurrogateId = ResourceSurrogateId&#xD;&#xA;&#x9;&#x9;FROM dbo.Resource WITH (UPDLOCK)&#xD;&#xA;&#x9;&#x9;WHERE ResourceTypeId = @resourceTypeId AND ResourceId = @resourceId" StatementId="4" StatementCompId="5" StatementType="SELECT" StatementSqlHandle="0x0900C1DA6F830DB21D973F591F8C01337E4E0000000000000000000000000000000000000000000000000000" DatabaseContextSettingsId="3" ParentObjectId="1234103437" StatementParameterizationType="0" RetrievedFromCache="true" StatementSubTreeCost="0.0032832" StatementEstRows="1" SecurityPolicyApplied="false" StatementOptmLevel="TRIVIAL" QueryHash="0x08A9E4B6AFA6CEB9" QueryPlanHash="0xF4DA5AF1E3F9C6B8" CardinalityEstimationModelVersion="140"><StatementSetOptions QUOTED_IDENTIFIER="true" ARITHABORT="false" CONCAT_NULL_YIELDS_NULL="true" ANSI_NULLS="true" ANSI_PADDING="true" ANSI_WARNINGS="true" NUMERIC_ROUNDABORT="false" /><QueryPlan CachedPlanSize="16" CompileTime="1" CompileCPU="1" CompileMemory="480"><MemoryGrantInfo SerialRequiredMemory="0" SerialDesiredMemory="0" /><OptimizerHardwareDependentProperties EstimatedAvailableMemoryGrant="2202003" EstimatedPagesCached="1101001" EstimatedAvailableDegreeOfParallelism="4" MaxCompileMemory="36877720" /><RelOp NodeId="0" PhysicalOp="Compute Scalar" LogicalOp="Compute Scalar" EstimateRows="1" EstimateIO="0" EstimateCPU="1e-07" AvgRowSize="19" EstimatedTotalSubtreeCost="0.0032832" Parallel="0" EstimateRebinds="0" EstimateRewinds="0" EstimatedExecutionMode="Row"><OutputList><ColumnReference Database="[jostairsfhirsk]" Schema="[dbo]" Table="[Resource]" Column="ResourceSurrogateId" /><ColumnReference Column="Expr1002" /></OutputList><ComputeScalar><DefinedValues><DefinedValue><ColumnReference Column="Expr1002" /><ScalarOperator ScalarString="[jostairsfhirsk].[dbo].[Resource].[Version]+(1)"><Arithmetic Operation="ADD"><ScalarOperator><Identifier><ColumnReference Database="[jostairsfhirsk]" Schema="[dbo]" Table="[Resource]" Column="Version" /></Identifier></Sca

## Index sizes

In [7]:
;with SpaceInfo(ObjectId, IndexId, TableName, IndexName
    ,Rows, TotalSpaceMB, UsedSpaceMB)
as
( 
    select  
        t.object_id as [ObjectId]
        ,i.index_id as [IndexId]
        ,s.name + '.' + t.Name as [TableName]
        ,i.name as [Index Name]
        ,sum(p.[Rows]) as [Rows]
        ,sum(au.total_pages) * 8 / 1024 as [Total Space MB]
        ,sum(au.used_pages) * 8 / 1024 as [Used Space MB]
    from    
        sys.tables t with (nolock) join 
            sys.schemas s with (nolock) on 
                s.schema_id = t.schema_id
            join sys.indexes i with (nolock) on 
                t.object_id = i.object_id
            join sys.partitions p with (nolock) on 
                i.object_id = p.object_id and 
                i.index_id = p.index_id
            cross apply
            (
                select 
                    sum(a.total_pages) as total_pages
                    ,sum(a.used_pages) as used_pages
                from sys.allocation_units a with (nolock)
                where p.partition_id = a.container_id 
            ) au
    where   
        i.object_id > 255
    group by
        t.object_id, i.index_id, s.name, t.name, i.name
)
select 
    ObjectId, IndexId, TableName, IndexName
    ,Rows, TotalSpaceMB, UsedSpaceMB
    ,TotalSpaceMB - UsedSpaceMB as [ReservedSpaceMB]
from 
    SpaceInfo		
order by
    TotalSpaceMB desc
option (recompile)

(14 rows affected)

Total execution time: 00:00:00.0980346

ObjectId IndexId TableName IndexName Rows TotalSpaceMB UsedSpaceMB ReservedSpaceMB 1058102810 1 dbo.Resource IXC_Resource 0 0 0 0 1058102810 2 dbo.Resource IX_Resource_ResourceSurrogateId 0 0 0 0 1074102867 1 dbo.DateSearchParam IXC_DateSearchParam 0 0 0 0 1090102924 1 dbo.NumberSearchParam IXC_NumberSearchParam 0 0 0 0 1106102981 1 dbo.QuantitySearchParam IXC_QuantitySearchParam 0 0 0 0 1106102981 2 dbo.QuantitySearchParam IXC_TokenSearchParam_SearchParamId_Code_System 0 0 0 0 1122103038 1 dbo.ReferenceSearchParam IXC_ReferenceSearchParam 0 0 0 0 1122103038 2 dbo.ReferenceSearchParam IX_ReferenceSearchParam_SearchParamId_BaseUri_ResourceId 0 0 0 0 1138103095 1 dbo.ResourceType Id_ResourceType 0 0 0 0 1170103209 0 dbo.SearchParam NULL 0 0 0 0 1186103266 1 dbo.StringSearchParam IXC_StringSearchParam 0 0 0 0 1202103323 1 dbo.TokenSearchParam IXC_TokenSearchParam 0 0 0 0 1202103323 2 dbo.TokenSearchParam IX_TokenSearchParam_SearchParamId_Code_System 0 0 0 0 1218103380 1 dbo.UriSearchParam IXC_UriSearchParam 0 0 0 0